# Extract information from PDF reports using LLM

Import necessary libraries

In [4]:
import os
import json

from langchain.vectorstores import FAISS, Chroma
from langchain.document_loaders import PyMuPDFLoader, PyPDFLoader, PDFMinerLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.prompts import PromptTemplate
from langchain.embeddings.openai import OpenAIEmbeddings

# Document Loading
Load the PDF document containing the financial report

In [5]:
# pdf file path
# pdf_file_path = "../../data/sylabus.pdf"
pdf_file_path = "../../data/HT_report.pdf"

In [6]:

# loader_mu = PyMuPDFLoader(pdf_file_path)

In [7]:

# loader_miner = PDFMinerLoader(pdf_file_path)

In [8]:
loader = PyPDFLoader(pdf_file_path)

ImportError: pypdf package not found, please install it with `pip install pypdf`

In [9]:
# print(loader_miner.load())

In [10]:
loader.load()

NameError: name 'loader' is not defined

In [11]:
documents = loader.load()
print(documents)
print(len(documents))

NameError: name 'loader' is not defined

In [12]:
# print(documents[70].page_content)

# Document Splitting
Initialize Recursive Text Splitter

In [13]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(
            chunk_size=1500,
            chunk_overlap=250,
            length_function = len
        )
print(text_splitter)


In [14]:
print(documents[39].page_content)

NameError: name 'documents' is not defined

In [15]:

docs = text_splitter.split_documents(documents)
print(len(docs))

NameError: name 'documents' is not defined

Let's make the chunks more readable

In [16]:
print(f"\n{'-' * 100}\n".join([f"Document {i+1}:\n\n" + d.page_content for i, d in enumerate(docs)]))


NameError: name 'docs' is not defined

# Embeddings and Vectorstore

Create Chroma db vectorstore with HuggingFace embeddings

In [ ]:
from langchain.vectorstores import FAISS, Chroma

vectordb = Chroma.from_documents(
    documents=docs,
    embedding=HuggingFaceEmbeddings(model_name="sentence-transformers/paraphrase-MiniLM-L6-v2"),
    persist_directory="../notebooks",
)
vectordb.persist()


Create Chroma db vectorstore with OpenAI embeddings

In [14]:
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import FAISS, Chroma

vectordb = Chroma.from_documents(
    documents=docs,
    embedding = OpenAIEmbeddings(),
    persist_directory="../notebooks",
    # collection_name="ht_report",
)
vectordb.persist()

In [15]:
print('\n\nCollection count is:', vectordb._collection.count())



Collection count is: 337


## Load vectorstore from disk

In [17]:
embedding_function = HuggingFaceEmbeddings(model_name="sentence-transformers/paraphrase-MiniLM-L6-v2")
vectordb = Chroma(
    persist_directory="../notebooks", 
    embedding_function=embedding_function,
    collection_name="hf_collection"
    )


c:\Users\ggvozden\Anaconda3\envs\semantic\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
embedding_function = OpenAIEmbeddings()
vectordb = Chroma(
    persist_directory="../notebooks", 
    embedding_function=embedding_function)

In [4]:
print('\n\nCollection count is:', vectordb._collection.count())



Collection count is: 337


## Retrieval

Similarity search - get the k most similar results to the query/question/message

In [18]:
def pretty_chunks(docs):
    print(f"\n{'-' * 100}\n".join([f"Document {i+1}:\n\n" + d.page_content for i, d in enumerate(docs)]))


In [19]:
query = "List the financial metrics like revenue, operating profit, comprehensive income from the consolidated statement of comprehensive for the year 2022."

In [20]:
results_ss = vectordb.similarity_search(query, k=3)
pretty_chunks(results_ss)

In [21]:
query = "List the financial metrics like revenue, operating profit, comprehensive income from the consolidated statement of comprehensive for the year 2022."

In [22]:
results_mmr=vectordb.max_marginal_relevance_search(query,k=3, fetch_k=15)
pretty_chunks(results_mmr)

In [23]:
from langchain.llms import OpenAI
llm = OpenAI(temperature=0, 
                openai_api_key=os.environ.get("OPENAI_API_KEY"),
                verbose=True
                )
                
from langchain.retrievers import ContextualCompressionRetriever
from langchain.retrievers.document_compressors import LLMChainExtractor

compressor = LLMChainExtractor.from_llm(llm)
compression_retriever = ContextualCompressionRetriever(
    base_compressor=compressor,
    base_retriever=vectordb.as_retriever()
)
compressed_docs = compression_retriever.get_relevant_documents(query)
pretty_chunks(compressed_docs)

In [24]:
print(compressed_docs)

[]


Initialize LLM model 

In [25]:
from langchain.llms import OpenAI
llm = OpenAI(temperature=0, 
                openai_api_key=os.environ.get("OPENAI_API_KEY"),
                verbose=True
                )

# Question & Answering
### Extraction through prompting

Consolidated Financial Statements represent the combined financial results and position of a parent company and its subsidiaries. This means they provide a comprehensive view of the financial health of an entire group of companies as opposed to just one company's standalone financial position. The purpose is to present, for the parent and its subsidiaries, financial information that is a reflection of the economic activities as if the group were a single economic entity


* Single economic entity view: By consolidating, users of the financial statement can see the total of what's owned and owed by the entire group.

* Avoid double counting: If a parent company has transactions with its subsidiaries, those transactions are eliminated in the consolidated statements to avoid inflating revenues, expenses, assets, or liabilities.

* Regulatory and standard setting bodies: Most jurisdictions, especially those that adhere to the International Financial Reporting Standards (IFRF) or U.S. Generally Accepted Accounting Principles (GAAP), require consolidated financial statements from parent companies for external reporting if they own more than a certain percentage of another company.

### Content of Consolidated Financial Statements:

#### Consolidated Balance Sheet (or Statement of Financial Position):

* Assets: What the group owns. This includes current assets (like cash, accounts receivable, inventories) and non-current assets (like property, plant, equipment, intangibles).
* Liabilities: What the group owes. This includes current liabilities (like accounts payable, short-term loans) and non-current liabilities (like long-term debt).
* Equity: Owner's share in the group. This includes issued capital, reserves, retained earnings, non-controlling interest (which represents the share of ownership in a subsidiary not held by the parent).
#### Consolidated Income Statement (or Statement of Comprehensive Income):

* Revenues: Incomes generated by the group.
* Expenses: Costs incurred to generate revenues.
* Profit or Loss: Difference between revenues and expenses.
* Other Comprehensive Income: Represents changes in equity during a period from transactions and other events from non-owner sources.
#### Consolidated Statement of Changes in Equity:

* Shows the movements in shareholders' equity over a period, including new share issues, dividends, and profit or loss for the period.
#### Consolidated Cash Flow Statement:

* Operating Activities: Cash flows from primary activities of the group.
* Investing Activities: Cash flows from acquiring and disposing of long-term assets.
* Financing Activities: Cash flows from activities that result in changes in the size and composition of the equity and borrowings of the entity.
* Notes to the Financial Statements:

These provide additional information about the figures in the financial statements. They can be about the accounting policies, breakdowns of certain figures, details about debt, and so forth.
To prepare consolidated financial statements, intercompany transactions (like sales from a parent to a subsidiary) are eliminated, and only external transactions are shown. Furthermore, the equity of the subsidiaries is replaced by the parent's investment in the subsidiaries and any non-controlling interests.

## HT Annual Report

## 1. Consolidated income statement key financial terms

In [4]:
query = "List the financial metrics from the consolidated statement of comprehensive for the year 2022."
# query = "Extract the financial metrics based on the Consolidated income statement for 2021"

from langchain.llms import OpenAI
llm = OpenAI(
    temperature=0, 
    openai_api_key=os.environ.get("OPENAI_API_KEY"),
    verbose=True
                )

In [5]:
question=query
# Build prompt
# # "Profit attributable to owners of the parent", "Profit attributable to non-controlling interests", "Earnings per share (EPS)", "Other comprehensive income that may be reclassified to profit or loss in subsequent periods"
template = """
Use provided context about consolidated income statement to answer the question. 
Provide the output in a structured machine readable JSON format. 
Year should be in integer format. The following financial key metrics: 

"Revenue", "Other operating income", "Merchandise, material and energy expenses", "Service expenses", 
"Employee benefits expenses", "Work performed by the Group and capitalized", "Depreciation and amortization",
"Impairment of non-current assets", "Net impairment losses on trade receivables and contract assets", "Other expenses",

"Operating profit", "Finance income", "Finance costs", "Finance costs – net",
"Finance costs – net", "Income tax expense", "Profit for the period", "Effects of foreign exchange", 
"Other comprehensive income / (loss) for the year, net of tax", "Total comprehensive income for the year"

are in string format and their values are in the float format.

If there isn't enough information say you don't know. Do not generate answers that don't use the source documents.
Always include the source name and page number for each fact you use in the response.  
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

In [6]:
query = "List the financial metrics from the consolidated statement of comprehensive for the year 2022."
question = query

template = """
Use the provided context about the consolidated income statement to answer the question. 
Your answer should be a structured JSON format, and you should extract:
- Key financial metrics
- Corresponding metric values
- Year
- And the official xbrl tags ONLY if they are defined by the IFRS taxonomy. 

CRUCIAL NOTE: Only use XBRL tags that are completely aligned with the IFRS taxonomy. If you are unsure, or if a metric might not have an official XBRL tag, put 'NA' or 'Not Available'. This is mandatory, and under no circumstances should a tag be guessed or created.

Ensure your answer is entirely based on the source documents.
Include the source name and page number for every fact you cite.

{context}
Question: {question}
Answer:
"""

QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

In [2]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    retriever=vectordb.as_retriever(),
    return_source_documents=True,
    chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})

NameError: name 'llm' is not defined

In [ ]:
# Print the structure of the result
print(result.keys())

dict_keys(['query', 'result', 'source_documents'])


In [116]:
# Print the source documents
print('\n\nResult is:', result)



Result is: {'query': 'List the financial metrics from the consolidated statement of comprehensive for the year 2022.', 'result': '[\n  {\n    "Metric": "Revenue",\n    "Value": 7410,\n    "Year": 2022,\n    "XBRL Tag": "Not Available"\n  },\n  {\n    "Metric": "Other operating income",\n    "Value": 107,\n    "Year": 2022,\n    "XBRL Tag": "Not Available"\n  },\n  {\n    "Metric": "Merchandise, material and energy expenses",\n    "Value": 1580,\n    "Year": 2022,\n    "XBRL Tag": "Not Available"\n  },\n  {\n    "Metric": "Service expenses",\n    "Value": 750,\n    "Year": 2022,\n    "XBRL Tag": "Not Available"\n  },\n  {\n    "Metric": "Employee benefits expenses",\n    "Value": 1137,\n    "Year": 2022,\n    "XBRL Tag": "Not Available"\n  },\n  {\n    "Metric": "Work performed by the Group and capitalized",\n    "Value": 70,\n    "Year": 2022,', 'source_documents': [Document(page_content='78 79CONSOLIDATED FINANCIAL STATEMENTS   CONSOLIDATED STATEMENT OF COMPREHENSIVE INCOME \nCONSOL

In [117]:
# Print the query and the answer
print('\nQuery:\n\n', query)
print('\nAnswer:', result["result"])


Query:

 List the financial metrics from the consolidated statement of comprehensive for the year 2022.

Answer: [
  {
    "Metric": "Revenue",
    "Value": 7410,
    "Year": 2022,
    "XBRL Tag": "Not Available"
  },
  {
    "Metric": "Other operating income",
    "Value": 107,
    "Year": 2022,
    "XBRL Tag": "Not Available"
  },
  {
    "Metric": "Merchandise, material and energy expenses",
    "Value": 1580,
    "Year": 2022,
    "XBRL Tag": "Not Available"
  },
  {
    "Metric": "Service expenses",
    "Value": 750,
    "Year": 2022,
    "XBRL Tag": "Not Available"
  },
  {
    "Metric": "Employee benefits expenses",
    "Value": 1137,
    "Year": 2022,
    "XBRL Tag": "Not Available"
  },
  {
    "Metric": "Work performed by the Group and capitalized",
    "Value": 70,
    "Year": 2022,


In [112]:
# Get the number of source documents
print('\n\nNumber of source documents is:', len(result["source_documents"]))
# Store the number of source documents in a variable len_source_docs
len_source_docs = len(result["source_documents"])
# Loop over the source documents and print the source number and page content 
for i in range(len_source_docs):
    print('\n\nSource number:', i)
    print('\nSource page content is:\n\n', result["source_documents"][i].page_content)

# Check the source documents
# print('\n\nSource documents are:\n\n', result["source_documents"][2].page_content)



Number of source documents is: 4


Source number: 0

Source page content is:

 78 79CONSOLIDATED FINANCIAL STATEMENTS   CONSOLIDATED STATEMENT OF COMPREHENSIVE INCOME 
CONSOLIDATED STATEMENT 
OF COMPREHENSIVE INCOME 
For the year ended 31 December 2022CONSOLIDATED STATEMENT OF 
COMPREHENSIVE INCOME  (CONTINUED)
For the year ended 31 December 2022
Notes 2022
HRK million2021
HRK million
Revenue 4 7,410 7,393
Other operating income 5 107 94
Merchandise, material and energy expenses 6 (1,580) (1,412)
Service expenses 7 (750) (822)
Employee benefits expenses 9 (1,137) (1,154)
Work performed by the Group and capitalized 70 79
Depreciation and amortization 8 (1,987) (2,266)
Impairment of non-current assets 8 (156) (63)
Net impairment losses on trade receivables and contract assets 23 (64) (68)
Other expenses 10 (967) (968)
Operating profit 4 946 813
Finance income 11 29 32
Finance costs 12 (91) (101)
Finance costs – net (62) (69)
Profit before income tax 884 744
Income tax expense 13 (224) 

Is it 'Profit attributable to owners of the parent' the same as the 'Profit attributable to Equity holders of the Company'? 

"Profit attributable to owners of the parent" and "Profit attributable to equity holders of the company" are effectively the same in financial reporting contexts. Both terms refer to the net profit (or loss) for a given period that belongs to the equity shareholders of the primary or parent company, as opposed to minority or non-controlling interests.

When a company has subsidiaries, and it consolidates its financial statements, there can be a portion of the profit that belongs to the parent company's shareholders and another portion that belongs to the non-controlling interests (also known as minority interests). The terminology used can vary based on the specific accounting standards followed (e.g., International Financial Reporting Standards or U.S. Generally Accepted Accounting Principles) and by region or jurisdiction.

### Save the extracted key financial metrics into a json file

In [43]:
# import json

# # Assuming result["result"] contains the string representation
# data_str = result["result"]

# # Load the string back to a dictionary
# data_dict = json.loads(data_str)

# # Now save the dictionary to a JSON file
# with open('financial_income_statement_metrics.json', 'w') as file:
#     json.dump(data_dict, file, indent=4)


In [44]:
# load financial_income_statement_metrics.json and pretty print it
with open('financial_income_statement_metrics.json') as json_file:
    data = json.load(json_file)
    print(json.dumps(data, indent=4))

{
    "Source": "HT Group Financial Statements, Page 78-79",
    "Year": 2021,
    "Revenue": 7393,
    "Other operating income": 94,
    "Merchandise, material and energy expenses": 1412,
    "Service expenses": 822,
    "Employee benefits expenses": 1154,
    "Work performed by the Group and capitalized": 79,
    "Depreciation and amortization": 2266,
    "Impairment of non-current assets": 63,
    "Net impairment losses on trade receivables and contract assets": 68,
    "Other expenses": 968,
    "Operating profit": 813,
    "Finance income": 32,
    "Finance costs": 101,
    "Finance costs \u2013 net": 69,
    "Income tax expense": 130,
    "Profit for the period": 614,
    "Effects of foreign exchange": 0,
    "Other comprehensive income / (loss) for the year, net of tax": 1,
    "Total comprehensive income for the year": 611
}


In [46]:
print(result.keys())

dict_keys(['query', 'result', 'source_documents'])


## 2. Consolidated balance sheets key financial terms for 2021

In [48]:
# query = "Display the consolidated income statement for the year 2021 and 2022."
query = "Extract the financial metrics based on the Consolidated balance sheet table for 2021"

from langchain.llms import OpenAI
llm = OpenAI(
    temperature=0, 
    openai_api_key=os.environ.get("OPENAI_API_KEY"),
    verbose=True
                )

In [60]:
question=query
# Build prompt
# "Intangible assets", "Property, plant and equipment", Non-current assets", Receivables, "Inventories", "Current assets",
# "Assets held for sale", "Total assets", "Equity attributable to owners of the parent", "Non-controlling interests",
# "Total equity", "Non-current liabilities", "Current liabilities", "Liabilities associated with assets held for sale"
# Include metric, value, IFRS xbrl tags, XBRL type, Substitution group, Data type, Standard label and accounting policy text.
template = """
Use provided context about consolidated balance sheet statement to answer the question.
Provide the output in a structured machine readable JSON format. 

Year should be in integer format. The following financial key metrics from balance sheet table should be extracted: 
"Intangible assets", "Property, plant and equipment" are in string format and their values are in the float format.
For each metric include xbrl tags according to IFRS taxonomy, XBRL type, Substitution group.

If there isn't enough information say you don't know. Do not generate answers that don't use the source documents.
Always include the source name and page number for each fact you use in the response.
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

In [61]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    retriever=vectordb.as_retriever(search_type="mmr", search_kwargs={'k': 7, 'fetch_k': 10}),
    # retriever=vectordb.as_retriever(),
    return_source_documents=True,
    chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})

In [62]:
# Print the structure of the result
print(result.keys())

dict_keys(['query', 'result', 'source_documents'])


In [63]:
# Print the source documents
print('\n\nResult is:', result)



Result is: {'query': 'Extract the financial metrics based on the Consolidated balance sheet table for 2021', 'result': '\n\n{\n  "Intangible assets": {\n    "value": 1898,\n    "source": "HT Group Financial Statements, Consolidated Balance Sheet, Page 65",\n    "xbrl_tags": "ifrs-full_IntangibleAssets",\n    "xbrl_type": "monetaryItemType",\n    "substitution_group": "ifrs-full_IntangibleAsset"\n  },\n  "Property, plant and equipment": {\n    "value": 6300,\n    "source": "HT Group Financial Statements, Consolidated Balance Sheet, Page 65",\n    "xbrl_tags": "ifrs-full_PropertyPlantAndEquipment",\n    "xbrl_type": "monetaryItemType",\n    "substitution_group": "ifrs-full_PropertyPlantAndEquipment"\n  }\n}', 'source_documents': [Document(page_content='Consolidated income statement\nConsolidated balance sheet\nConsolidated cash flow statementHT GROUP FINAN-CIAL STATE -MENTS', metadata={'page': 31, 'source': '../../data/HT_report.pdf'}), Document(page_content='The consolidated financial

In [64]:
# Print the query and the answer
print('\nQuery:\n\n', query)
print('\nAnswer:', result["result"])


Query:

 Extract the financial metrics based on the Consolidated balance sheet table for 2021

Answer: 

{
  "Intangible assets": {
    "value": 1898,
    "source": "HT Group Financial Statements, Consolidated Balance Sheet, Page 65",
    "xbrl_tags": "ifrs-full_IntangibleAssets",
    "xbrl_type": "monetaryItemType",
    "substitution_group": "ifrs-full_IntangibleAsset"
  },
  "Property, plant and equipment": {
    "value": 6300,
    "source": "HT Group Financial Statements, Consolidated Balance Sheet, Page 65",
    "xbrl_tags": "ifrs-full_PropertyPlantAndEquipment",
    "xbrl_type": "monetaryItemType",
    "substitution_group": "ifrs-full_PropertyPlantAndEquipment"
  }
}


In [65]:
# Get the number of source documents
print('\n\nNumber of source documents is:', len(result["source_documents"]))
# Store the number of source documents in a variable len_source_docs
len_source_docs = len(result["source_documents"])
# Loop over the source documents and print the source number and page content 
for i in range(len_source_docs):
    print('\n\nSource number:', i)
    print('\nSource page content is:\n\n', result["source_documents"][i].page_content)

# Check the source documents
# print('\n\nSource documents are:\n\n', result["source_documents"][2].page_content)



Number of source documents is: 7


Source number: 0

Source page content is:

 Consolidated income statement
Consolidated balance sheet
Consolidated cash flow statementHT GROUP FINAN-CIAL STATE -MENTS


Source number: 1

Source page content is:

 The consolidated financial statements for the financial year end-
ed 31 December 2022 were authorized for issue in accordance 
with a resolution of the Management Board on 14 March 2023. 
These consolidated financial statements are subject to approval 
Due to loss of control in July 2021, Optima Telekom is deconsolidated from statements of HT Group for 2021. In 2022, the sale process of 
Optima shares is closed.Ownership interest
Entity Country of Business Principal Activities31 December
202231 December 
2021
Combis d.o.o. Republic of Croatia Provision of IT services 100% 100%
Iskon Internet d.d. Republic of CroatiaProvision of internet and data 
services100% 100%
OT-Optima Telekom d.d. /i/ Republic of CroatiaProvision of internet and data 


### Save the extracted key financial metrics into a json file

In [66]:
import json

# Assuming result["result"] contains the string representation
data_str = result["result"]

# Load the string back to a dictionary
data_dict = json.loads(data_str)

# Now save the dictionary to a JSON file
with open('consolidated_balance_sheet.json', 'w') as file:
    json.dump(data_dict, file, indent=4)


In [67]:
# load financial_income_statement_metrics.json and pretty print it
with open('consolidated_balance_sheet.json') as json_file:
    data = json.load(json_file)
    print(json.dumps(data, indent=4))

{
    "Intangible assets": {
        "value": 1898,
        "source": "HT Group Financial Statements, Consolidated Balance Sheet, Page 65",
        "xbrl_tags": "ifrs-full_IntangibleAssets",
        "xbrl_type": "monetaryItemType",
        "substitution_group": "ifrs-full_IntangibleAsset"
    },
    "Property, plant and equipment": {
        "value": 6300,
        "source": "HT Group Financial Statements, Consolidated Balance Sheet, Page 65",
        "xbrl_tags": "ifrs-full_PropertyPlantAndEquipment",
        "xbrl_type": "monetaryItemType",
        "substitution_group": "ifrs-full_PropertyPlantAndEquipment"
    }
}


In [68]:
print(result.keys())

dict_keys(['query', 'result', 'source_documents'])


## 3. Consolidated cash flow key financial terms for 2021

In [117]:
# query = "Display the consolidated income statement for the year 2021 and 2022."
query = "Extract the financial figures and values from consolidated statement of cash flow for 2021"

In [118]:
question=query
# Build prompt
template = """
You are a provided with the context about consolidated statement of cash flow to answer the question. 
Provide the output in a machine readable JSON format.
Year should be in YYYY integer format. Financial key metrics are in string format and their values are in the float format.
If there isn't enough information say you don't know. Do not generate answers that don't use the source documents.
Always include the source name and page number for each fact you use in the response.

        
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

In [119]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    retriever=vectordb.as_retriever(),
    return_source_documents=True,
    chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})
print('\n\nQuery:\n\n', query)
print('\n\nAnswer:\n', result["result"])



Query:

 Extract the financial figures and values from consolidated statement of cash flow for 2021


Answer:
 

{
    "Source": "Consolidated Statement of Cash Flows, Page 82-83",
    "Year": 2021,
    "Financial Figures": {
        "Interest Income": -8.0,
        "Interest Expense": 71.0,
        "Gain on Disposal of Assets": -13.0,
        "Other Net Financial Loss": 6.0,
        "Increase in Inventories": -39.0,
        "Increase in Receivables and Prepayments": 182.0,
        "Increase in Contract Assets/Costs": -29.0,
        "Increase in Payables and Accruals": -199.0,
        "Increase in Contract Liabilities": 17.0,
        "Increase in Provisions": 0.0,
        "Increase in Employee Benefit Obligations": 0.0,
        "Increase in Accruals": 6.0,
        "Other Non-Cash Items": -7.0,
        "Cash Generated from Operations": 3117.0,
        "Interest Paid": 78.0,
        "Income Tax Paid": 177.0,
       


In [120]:
# Assuming result["result"] contains the string representation
data_str = result["result"]

# Load the string back to a dictionary
data_dict = json.loads(data_str)
    
# Sve the result dictionary to a JSON file
with open('financial_cash_flow_metrics.json', 'w') as file:
    json.dump(data_dict, file, indent=4)

# Load and pretty print the JSON file
with open('financial_cash_flow_metrics.json') as json_file:
    data = json.load(json_file)
    print(json.dumps(data, indent=4))

JSONDecodeError: Expecting property name enclosed in double quotes: line 23 column 8 (char 816)

## Extract each financial position and corresponding values and metadata

In [ ]:
# Define the question
query = "List the financial metrics from the consolidated statement of comprehensive income for the year 2022."

In [118]:
# Load the IFRS taxonomy from the Excel file into a DataFrame
taxonomy_df = pd.read_excel('taxonomy-iti-2023-by-fs.xlsx')

# Define the function to save the results to a JSON file
def save_to_json(data, filename="income_statement_all.json"):
    with open(filename, 'w') as file:
        json.dump(data, file, indent=4)

# Define a function to save the results to a CSV and Excel file
def save_to_csv_excel(results, csv_filename="results.csv", excel_filename="results.xlsx"):
    """
    Save the results to a CSV and Excel file.
    
    :param results: Dictionary with financial metrics as keys and dictionaries with details as values.
    :param csv_filename: Name of the output CSV file.
    :param excel_filename: Name of the output Excel file.
    """

    # Convert the string representation back to dictionaries
    list_of_dicts = [json.loads(result) for result in results]

    # Convert the list of dictionaries into a DataFrame
    df = pd.DataFrame(list_of_dicts)

    # Save to CSV
    df.to_csv("results.csv", index=False)

    # Save to Excel
    df.to_excel("results.xlsx", engine='openpyxl', index=False)

import pandas as pd

# List of financial terms
financial_metric = ["Sales Revenue", "Other operating income", "Merchandise, material and energy expenses", "Service expenses", "Employee benefits expenses"]

# financial_metric = [
#     "Revenue", "Other operating income", "Merchandise, material and energy expenses", "Service expenses", 
#     "Employee benefits expenses", "Work performed by the Group and capitalized", "Depreciation and amortization",
#     "Impairment of non-current assets", "Net impairment losses on trade receivables and contract assets", "Other expenses",
#     "Operating profit", "Finance income", "Finance costs", "Finance costs net", 
#     "Finance costs net", "Income tax expense", "Profit for the period", "Effects of foreign exchange", 
#     "Other comprehensive income / (loss) for the year, net of tax", "Total comprehensive income for the year, net of tax",
#     "Profit attributable to owners of the parent", "Profit attributable to non-controlling interests", 
#     "Total comprehensive income arisen from continuing operations attributable to owners of the parent", 
#     "Total comprehensive income arisen from continuing operations attributable to non-controlling interests"
# ]

# Define the prompt template outside the loop to avoid redundant object creation.
template = """Based on provided context, answer and extract information about the financial metric.
The output should be in a machine-readable structured JSON format.
The output should contain the followint:
metric value in type float and without brackets, 
currency, 
corresponding xbrl tag according to ifrs taxonomy (e.g. ifrs-full:Revenue)),
ifrs taxonomy substitution group (Substituion group- xbrli:item)
ifrs taxonomy data type (e.g. monetary, string, share, decimal, etc.),
ifrs balance type (e.g. debit, credit, etc.),
source name and page number for each fact used in the response.

CRUCIAL NOTE: Only use XBRL tags that are completely aligned with the IFRS taxonomy. If you are unsure, or if a metric might not have an official XBRL tag, put 'NA' or 'Not Available'. This is mandatory, and under no circumstances should a tag be guessed or created.

{context}
Question: {question}
Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

# Initialize the qa_chain object outside the loop.
qa_chain = RetrievalQA.from_chain_type(
        llm,
        # chain_type="stuff",
        retriever=vectordb.as_retriever(search_type="mmr", search_kwargs={'k': 7, 'fetch_k': 10}),
        return_source_documents=True,
        chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
        )

# A dictionary to store results for all terms
results = []

# Loop through the financial terms and extract the information
for metric in financial_metric:
    print('\nFinancial metric:', metric)
    
    # Formulate the question
    # question = f"Extract the {metric} from the consolidated income statement for 2021"
    # question = f"What is the {metric} in the consolidated statement of comprehensive income for the year 2022?"
    question = f"List the financial metrics from the consolidated statement of comprehensive income for the year 2022 and extract {metric}."
    print('The question is:', question)

    # Obtain the result
    result = qa_chain({"query": question})

    # Store the result in the results dictionary with term as the key
    results.append(result["result"])

    print('\nResult is:', result["result"])

save_to_json(results)
save_to_csv_excel(results, "results.csv", "results.xlsx")



Financial metric: Sales Revenue
The question is: List the financial metrics from the consolidated statement of comprehensive income for the year 2022 and extract Sales Revenue.

Result is:  
{
    "metric": "Sales Revenue",
    "value": 7410.0,
    "currency": "HRK million",
    "xbrl_tag": "ifrs-full:Revenue",
    "substitution_group": "xbrli:item",
    "data_type": "monetary",
    "balance_type": "credit",
    "source_name": "Consolidated Statement of Comprehensive Income",
    "page_number": "78-79"
}

Financial metric: Other operating income
The question is: List the financial metrics from the consolidated statement of comprehensive income for the year 2022 and extract Other operating income.

Result is:  
{
    "metric_value": 107,
    "currency": "HRK million",
    "xbrl_tag": "ifrs-full:OtherOperatingIncome",
    "substitution_group": "xbrli:item",
    "data_type": "monetary",
    "balance_type": "credit",
    "source_name": "Notes to the Consolidated Financial Statements",
   

## Transform the taxonomy dataframe for furher processing

In [13]:
# Load the second sheet IFRS taxonomy from the Excel file into a DataFrame
taxonomy_df = pd.read_excel('taxonomy-iti-2023-by-fs.xlsx', sheet_name=1)
taxonomy_df.head()

Concept name  \
0  [110000] General information about financial s...   
1  DisclosureOfGeneralInformationAboutFinancialSt...   
2  NameOfReportingEntityOrOtherMeansOfIdentification   
3  ExplanationOfChangeInNameOfReportingEntityOrOt...   
4           DescriptionOfNatureOfFinancialStatements   

                                     Preferred label  \
0  https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-...   
1  Disclosure of general information about financ...   
2  Name of reporting entity or other means of ide...   
3  Explanation of change in name of reporting ent...   
4      Description of nature of financial statements   

                                      Standard label  \
0                                                NaN   
1  Disclosure of general information about financ...   
2  Name of reporting entity or other means of ide...   
3  Explanation of change in name of reporting ent...   
4      Description of nature of financial statements   

                                 Documentation label Guidance label  \
0                                                NaN            NaN   
1  The entire disclosure for general information ...            NaN   
2  The name of the reporting entity or other mean...            NaN   
3  The explanation of the change in either the na...            NaN   
4  The description of the nature of financial sta...            NaN   

         Type                                         References  \
0         NaN                                                NaN   
1  Text block                                IAS 1.51 Disclosure   
2        Text                              IAS 1.51 a Disclosure   
3        Text                              IAS 1.51 a Disclosure   
4        Text  IAS 1.51 b Disclosure, IAS 27.16 a Disclosure,...   

                                     Reference Links  
0                                                NaN  
1  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
2  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
3  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
4  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...

In [26]:
import pandas as pd

# Create a mask for rows that represent a new group (i.e., they have a URL in the 'Preferred label' column)
mask = taxonomy_df['Preferred label'].str.startswith('https://')

# Use the mask to create a new column 'concept_name' that has the 'Concept name' value for each group
taxonomy_df['concept_name'] = taxonomy_df.loc[mask, 'Concept name']
taxonomy_df['concept_name_url'] = taxonomy_df.loc[mask, 'Preferred label']

# Forward fill to propagate the group 'Concept name' to the following rows
taxonomy_df['concept_name'] = taxonomy_df['concept_name'].ffill()
taxonomy_df['concept_name_url'] = taxonomy_df['concept_name_url'].ffill()

# # Extract the xbrl_item from the preferred_label by removing text in square brackets
# taxonomy_df['xbrl_item'] = taxonomy_df['Preferred label'].str.replace(r' \[.*\]', '', regex=True)
# Create the xbrl_item column by removing the square brackets from the 'preferred_label' column
taxonomy_df['xbrl_item'] = taxonomy_df['Preferred label'].str.replace(r'\[|\]', '', regex=True)

# Create a new DataFrame in the desired format
result_df = pd.DataFrame({
    'concept_name': taxonomy_df['concept_name'],
    'concept_name_url': taxonomy_df['concept_name_url'],
    'xbrl_tag': taxonomy_df['Concept name'],
    'preferred_label': taxonomy_df['Preferred label'],
    'xbrl_item': taxonomy_df['xbrl_item'],
    'standard_label': taxonomy_df['Standard label'],
    'documentation_label': taxonomy_df['Documentation label'],
    'guidance_label': taxonomy_df['Guidance label'],
    'type': taxonomy_df['Type'],
    'references': taxonomy_df['References'],
    'reference_links': taxonomy_df['Reference Links']
})

# Remove rows that were used to identify groups (because they have now been propagated to the following rows)
result_df = result_df[~mask]

# Reset index
result_df = result_df.reset_index(drop=True)

# Display the result
result_df.head()

# Save the result to a CSV file
result_df.to_csv('taxonomy.csv', index=False)

# Save the result to an Excel file taxonomy-iti-2023-by-fs.xlsx sheet name 'transformed'
result_df.to_excel('taxonomy_xbrl_2023.xlsx', sheet_name='transformed', index=False)

# Load the second sheet IFRS taxonomy from the Excel file into a DataFrame
taxonomy_xbrl = pd.read_excel('taxonomy_xbrl_2023.xlsx')
taxonomy_xbrl.head()


concept_name  \
0  [110000] General information about financial s...   
1  [110000] General information about financial s...   
2  [110000] General information about financial s...   
3  [110000] General information about financial s...   
4  [110000] General information about financial s...   

                                    concept_name_url  \
0  https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-...   
1  https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-...   
2  https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-...   
3  https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-...   
4  https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-...   

                                            xbrl_tag  \
0  DisclosureOfGeneralInformationAboutFinancialSt...   
1  NameOfReportingEntityOrOtherMeansOfIdentification   
2  ExplanationOfChangeInNameOfReportingEntityOrOt...   
3           DescriptionOfNatureOfFinancialStatements   
4                     DateOfEndOfReportingPeriod2013   

                                     preferred_label  \
0  Disclosure of general information about financ...   
1  Name of reporting entity or other means of ide...   
2  Explanation of change in name of reporting ent...   
3      Description of nature of financial statements   
4                    Date of end of reporting period   

                                           xbrl_item  \
0  Disclosure of general information about financ...   
1  Name of reporting entity or other means of ide...   
2  Explanation of change in name of reporting ent...   
3      Description of nature of financial statements   
4                    Date of end of reporting period   

                                      standard_label  \
0  Disclosure of general information about financ...   
1  Name of reporting entity or other means of ide...   
2  Explanation of change in name of reporting ent...   
3      Description of nature of financial statements   
4                    Date of end of reporting period   

                                 documentation_label guidance_label  \
0  The entire disclosure for general information ...            NaN   
1  The name of the reporting entity or other mean...            NaN   
2  The explanation of the change in either the na...            NaN   
3  The description of the nature of financial sta...            NaN   
4       The date of the end of the reporting period.            NaN   

         type                                         references  \
0  Text block                                IAS 1.51 Disclosure   
1        Text                              IAS 1.51 a Disclosure   
2        Text                              IAS 1.51 a Disclosure   
3        Text  IAS 1.51 b Disclosure, IAS 27.16 a Disclosure,...   
4        Date                              IAS 1.51 c Disclosure   

                                     reference_links  
0  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
1  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
2  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
3  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...  
4  https://taxonomy.ifrs.org/xifrs-link?type=IAS&...

In [27]:
# Check the number of unique values in the xbrl_item column
print('\n\nNumber of unique values in the xbrl_item column is:', taxonomy_xbrl.xbrl_item.nunique())

# Check the number of unique values in the preferred_label column
print('\n\nNumber of unique values in the preferred_label column is:', taxonomy_xbrl.preferred_label.nunique())

# # Check the number of unique values in the xbrl_tag column
# print('\n\nNumber of unique values in the xbrl_tag column is:', taxonomy_xbrl.xbrl_tag.nunique())

# # Check the number of unique values in the concept_name column
# print('\n\nNumber of unique values in the concept_name column is:', taxonomy_xbrl.concept_name.nunique())

# # Check the number of unique values in the concept_name_url column
# print('\n\nNumber of unique values in the concept_name_url column is:', taxonomy_xbrl.concept_name_url.nunique())



Number of unique values in the xbrl_item column is: 5151


Number of unique values in the preferred_label column is: 5151


### Check the frequency distribution for newly created column

In [39]:
# Display the frequency of the xbrl_item column
print('\n\nFrequency of the xbrl_item column is:\n\n', taxonomy_xbrl.xbrl_item.value_counts())

# Display the frequency of the preferred_label column
print('\n\nFrequency of the preferred_label column is:\n\n', taxonomy_xbrl.preferred_label.value_counts())  




Frequency of the xbrl_item column is:

 Aggregated time bands member                                                                                                                                                                       16
Maturity axis                                                                                                                                                                                      16
Derivatives member                                                                                                                                                                                 13
Measurement axis                                                                                                                                                                                   12
Aggregated measurement member                                                                                                                                         

## Transform the selected columns of interest into the vector space

In [40]:
from langchain.document_loaders.csv_loader import CSVLoader

In [41]:
loader = CSVLoader(file_path="../notebooks/taxonomy.csv")
data = loader.load()

In [36]:
print(data)

[Document(page_content='concept_name: [110000] General information about financial statements\nconcept_name_url: https://xbrl.ifrs.org/role/ifrs/ias_1_2023-03-23_role-110000\nxbrl_tag: DisclosureOfGeneralInformationAboutFinancialStatementsExplanatory\npreferred_label: Disclosure of general information about financial statements [text block]\nxbrl_item: Disclosure of general information about financial statements text block\nstandard_label: Disclosure of general information about financial statements [text block]\ndocumentation_label: The entire disclosure for general information about financial statements.\nguidance_label: \ntype: Text block\nreferences: IAS\xa01.51\xa0Disclosure\nreference_links: https://taxonomy.ifrs.org/xifrs-link?type=IAS&num=1&code=ifrs-tx-2023-en-r&anchor=para_51&doctype=Standard', metadata={'source': '../notebooks/taxonomy.csv', 'row': 0}), Document(page_content='concept_name: [110000] General information about financial statements\nconcept_name_url: https://xbr

Customize CSV and load

In [42]:
print(len(data))

7155


In [ ]:
loader = CSVLoader(
    file_path="../notebooks/taxonomy.csv",
    csv_args={
        "delimiter": ",",
        "quotechar": '"',
        "fieldnames": ["MLB Team", "Payroll in millions", "Wins"],
    },
)

data = loader.load()

In [76]:
def format_data_content(entry):
    # Split the page_content by newline characters to get individual attributes
    attributes = entry.page_content.split('\n')
    
    # Format each attribute for better readability
    formatted_attributes = [attr.replace(':', ': ') for attr in attributes]
    
    # Add the metadata source to the formatted attributes
    formatted_attributes.append('Metadata source: ' + entry.metadata['source'])
    
    # Join the formatted attributes with newline characters and return the result
    return '\n'.join(formatted_attributes)

# Example usage:
i = 2  # You can change this to any index you want
print(format_data_content(data[i]))


concept_name:  [110000] General information about financial statements
concept_name_url:  https: //xbrl.ifrs.org/role/ifrs/ias_1_2023-03-23_role-110000
xbrl_tag:  ExplanationOfChangeInNameOfReportingEntityOrOtherMeansOfIdentificationFromEndOfPrecedingReportingPeriod
preferred_label:  Explanation of change in name of reporting entity or other means of identification from end of preceding reporting period
xbrl_item:  Explanation of change in name of reporting entity or other means of identification from end of preceding reporting period
standard_label:  Explanation of change in name of reporting entity or other means of identification from end of preceding reporting period
documentation_label:  The explanation of the change in either the name of the reporting entity or any other means of identification from the end of the preceding reporting period.
guidance_label:  
type:  Text
references:  IAS 1.51 a Disclosure
reference_links:  https: //taxonomy.ifrs.org/xifrs-link?type=IAS&num=1&code

## Create vectorstore

In [77]:
from langchain.vectorstores import FAISS, Chroma

vectordb = Chroma.from_documents(
    documents=data,
    embedding=HuggingFaceEmbeddings(model_name="sentence-transformers/paraphrase-MiniLM-L6-v2"),
    persist_directory="../notebooks/taxonomy/",
    collection_name="taxonomy_collection"
)

vectordb.persist()

## Load vectorstore

In [ ]:
# Load the persisted vectorstore

embedding_function = HuggingFaceEmbeddings(model_name="sentence-transformers/paraphrase-MiniLM-L6-v2")
vectordb = Chroma(
    persist_directory="../notebooks/taxonomy/", 
    embedding_function=embedding_function,
    collection_name="taxonomy_collection"
    )

## Similarity check

In [91]:

query = "The amount of expenses arising from a group of insurance contracts issued, comprising incurred claims (excluding repayments of investment components), other incurred insurance service expenses, amortisation of insurance"
docs = vectordb.similarity_search(query,k=2)

for doc in docs:
    print(format_data_content(doc))
    print('-' * 100)  

# print(docs)

concept_name:  [836600] Notes - Insurance contracts (IFRS 17)
concept_name_url:  https: //xbrl.ifrs.org/role/ifrs/ifrs_17_2023-03-23_role-836600
xbrl_tag:  InsuranceRevenue
preferred_label:  Total insurance revenue
xbrl_item:  Total insurance revenue
standard_label:  Insurance revenue
documentation_label:  The amount of revenue arising from the groups of insurance contracts issued. Insurance revenue shall depict the provision of services arising from the group of insurance contracts at an amount that reflects the consideration to which the entity expects to be entitled in exchange for those services. [Refer:  Insurance contracts issued [member]; Revenue]
guidance_label:  
type:  Monetaryduration, credit
references:  IAS 1.82 a (ii) Disclosure, IFRS 17.106 Disclosure, IFRS 17.80 a Disclosure
reference_links:  https: //taxonomy.ifrs.org/xifrs-link?type=IAS&num=1&code=ifrs-tx-2023-en-r&anchor=para_82_a_ii&doctype=Standard
https: //taxonomy.ifrs.org/xifrs-link?type=IFRS&num=17&code=ifrs-tx

In [93]:

query = "The amount of expenses arising from a group of insurance contracts issued, comprising incurred claims (excluding repayments of investment components), other incurred insurance service expenses, amortisation of insurance"
docs = vectordb.similarity_search_with_relevance_scores(query,k=2)



print(docs)

[(Document(page_content='concept_name: [836600] Notes - Insurance contracts (IFRS 17)\nconcept_name_url: https://xbrl.ifrs.org/role/ifrs/ifrs_17_2023-03-23_role-836600\nxbrl_tag: InsuranceRevenue\npreferred_label: Total insurance revenue\nxbrl_item: Total insurance revenue\nstandard_label: Insurance revenue\ndocumentation_label: The amount of revenue arising from the groups of insurance contracts issued. Insurance revenue shall depict the provision of services arising from the group of insurance contracts at an amount that reflects the consideration to which the entity expects to be entitled in exchange for those services. [Refer: Insurance contracts issued [member]; Revenue]\nguidance_label: \ntype: Monetaryduration, credit\nreferences: IAS\xa01.82\xa0a\xa0(ii)\xa0Disclosure, IFRS\xa017.106\xa0Disclosure, IFRS\xa017.80\xa0a\xa0Disclosure\nreference_links: https://taxonomy.ifrs.org/xifrs-link?type=IAS&num=1&code=ifrs-tx-2023-en-r&anchor=para_82_a_ii&doctype=Standard\nhttps://taxonomy.i

In [87]:

query = "Insurance revenue in telecommunication industry"
docs = vectordb.max_marginal_relevance_search(query, k=3, fetch_k=15)

for doc in docs:
    print(format_data_content(doc))
    print('-' * 100)  

# print(docs)

concept_name:  [320000] Statement of comprehensive income, profit or loss, by nature of expense
concept_name_url:  https: //xbrl.ifrs.org/role/ifrs/ias_1_2023-03-23_role-320000
xbrl_tag:  InsuranceRevenue
preferred_label:  Insurance revenue
xbrl_item:  Insurance revenue
standard_label:  Insurance revenue
documentation_label:  The amount of revenue arising from the groups of insurance contracts issued. Insurance revenue shall depict the provision of services arising from the group of insurance contracts at an amount that reflects the consideration to which the entity expects to be entitled in exchange for those services. [Refer:  Insurance contracts issued [member]; Revenue]
guidance_label:  
type:  Monetaryduration, credit
references:  IAS 1.82 a (ii) Disclosure, IFRS 17.106 Disclosure, IFRS 17.80 a Disclosure
reference_links:  https: //taxonomy.ifrs.org/xifrs-link?type=IAS&num=1&code=ifrs-tx-2023-en-r&anchor=para_82_a_ii&doctype=Standard
https: //taxonomy.ifrs.org/xifrs-link?type=IFRS

# Retreival and mapping of financial positions to IFRS taxonomy

In [125]:


# Define the function to save the results to a JSON file
def save_to_json(data, filename="income_statement_all.json"):
    with open(filename, 'w') as file:
        json.dump(data, file, indent=4)

# Define a function to save the results to a CSV and Excel file
def save_to_csv_excel(results, csv_filename="results.csv", excel_filename="results.xlsx"):
    """
    Save the results to a CSV and Excel file.
    
    :param results: Dictionary with financial metrics as keys and dictionaries with details as values.
    :param csv_filename: Name of the output CSV file.
    :param excel_filename: Name of the output Excel file.
    """

    # Convert the string representation back to dictionaries
    list_of_dicts = [json.loads(result) for result in results]

    # Convert the list of dictionaries into a DataFrame
    df = pd.DataFrame(list_of_dicts)

    # Save to CSV
    df.to_csv("results.csv", index=False)

    # Save to Excel
    df.to_excel("results.xlsx", engine='openpyxl', index=False)



# Define the prompt template outside the loop to avoid redundant object creation.
template = """Based on provided context, answer and extract information about the financial metric.
The output should be in a machine-readable structured JSON format.
The output should contain the following:
metric value in type float and without brackets, 
currency, 
corresponding xbrl tag according to ifrs taxonomy (e.g. ifrs-full:Revenue)),
ifrs taxonomy substitution group (Substituion group- xbrli:item)
ifrs taxonomy data type (e.g. monetary, string, share, decimal, etc.),
ifrs balance type (e.g. debit, credit, etc.),
source name and page number for each fact used in the response.

CRUCIAL NOTE: Only use XBRL tags that are completely aligned with the IFRS taxonomy. If you are unsure, or if a metric might not have an official XBRL tag, put 'NA' or 'Not Available'. This is mandatory and under no circumstances should a tag be guessed or created.

{context}
Question: {question}
Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

# Initialize the qa_chain object outside the loop.
qa_chain = RetrievalQA.from_chain_type(
        llm,
        # chain_type="stuff",
        retriever=vectordb.as_retriever(search_type="mmr", search_kwargs={'k': 7, 'fetch_k': 10}),
        return_source_documents=True,
        chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
        )

# A dictionary to store results for all terms
results = []

# Loop through the financial terms and extract the information
for metric in financial_metric:
    print('\nFinancial metric:', metric)
    
    # Formulate the question
    # question = f"Extract the {metric} from the consolidated income statement for 2021"
    # question = f"What is the {metric} in the consolidated statement of comprehensive income for the year 2022?"
    question = f"List the financial metrics from the consolidated statement of comprehensive income for the year 2022 and extract {metric}."
    print('The question is:', question)

    # Obtain the result
    result = qa_chain({"query": question})

    # Store the result in the results dictionary with term as the key
    results.append(result["result"])

    print('\nResult is:', result["result"])

save_to_json(results)
save_to_csv_excel(results, "results.csv", "results.xlsx")

# A dictionary to store results for all terms
results = []

# Loop through the financial terms and extract the information
for metric in financial_metric:
    print('\nFinancial metric:', metric)
    
    # Formulate the question
    # question = f"Extract the {metric} from the consolidated income statement for 2021"
    # question = f"What is the {metric} in the consolidated statement of comprehensive income for the year 2022?"
    question = f"{metric}"
    print('The question is:', question)

    # Obtain the result
    result = qa_chain({"query": question})

    # Store the result in the results dictionary with term as the key
    results.append(result["result"])

    print('\nResult is:', result["result"])

save_to_json(results)
# save_to_csv_excel(results, "results.csv", "results.xlsx")



Financial metric: The amount of assets representing the future economic benefits arising from other assets acquired in a business combination that are not individually identified and separately recognised
The question is: The amount of assets representing the future economic benefits arising from other assets acquired in a business combination that are not individually identified and separately recognised

Result is: 
{
    "metric_value": 0.00,
    "currency": "NA",
    "xbrl_tag": "NA",
    "substitution_group": "NA",
    "data_type": "NA",
    "balance_type": "NA",
    "source_name": "NA",
    "page_number": "NA"
}


In [123]:
print('\n\nResults are:', results)



Results are: ['\n{\n    "metric_value": 0.00,\n    "currency": "NA",\n    "xbrl_tag": "NA",\n    "substitution_group": "xbrli:item",\n    "data_type": "monetary",\n    "balance_type": "NA",\n    "source_name": "NA",\n    "page_number": "NA"\n}']


In [67]:
import json

# Convert the string representation back to dictionaries
list_of_dicts = [json.loads(result) for result in results]

# Convert the list of dictionaries into a DataFrame
df = pd.DataFrame(list_of_dicts)

# Save to CSV
df.to_csv("results.csv", index=False)

# Save to Excel
df.to_excel("results.xlsx", engine='openpyxl', index=False)

## Prompt variation

In [127]:
query = "Extract the financial metric 'Goodwill'?"

In [131]:
question=query
# Build prompt
template = """Given a text, please extract the financial data..
The final output should be a structured JSON representation. Provide the xbrl tags according to ESEF taxonomy.
Always include the source name and page number for all appearings of the 'Goodwill' you use in the response.
Provide the result and structure it into a machine-readable JSON format
{context}
Question: {question}
Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)



In [132]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    chain_type="refine",
    retriever=vectordb.as_retriever(search_type="mmr", search_kwargs={'k': 8, 'fetch_k': 50}),
    return_source_documents=True,
    # chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})

In [133]:
# print result
print('\nResult structure:\n\n', result.keys())
print('\nResult:\n\n', result)
print('\n\nQuery:\n\n', query)
print('\n\nAnswer:\n\n', result["result"])
print('\n\nSource documents:\n\n', len(result["source_documents"]))


Result structure:

 dict_keys(['query', 'result', 'source_documents'])

Result:

 {'query': "Extract the financial metric 'Goodwill'?", 'result': '\n\nGoodwill of HRK 347 million, as disclosed in the table under the contractual undiscounted cash flows and in the Intangible Assets section of the financial statement, with a net book value of HRK 434 million as of 1 January 2021 and HRK 463 million as of 31 December 2021, is recognized in the balance sheet as a contract asset, which is amortized over the remaining term of the contract and, compared with the amounts invoiced, reduces the revenue. The expected credit loss measurement is based on reasonable and supporting information that is available without additional expenses and effort, including information on past events, current and foreseeable future conditions and circumstances. The measurement of expected loss is linked to macroeconomic data and historical customer behaviour, which is corrected under certain conditions.', 'source_

## Prompt variation

In [78]:
query = "Based on the consolidated income statement, spanning multiple years, extract all financial figures for each year and structure it into a machine-readable JSON format."

In [79]:
question=query
# Build prompt
template = """You have a role of a Financial Data Analyst: With a keen eye for numbers and the intricacies of financial statements, 
you specialize in extracting, analyzing and structuring financial data. Your expertise ensures that critical financial metrics from provided context are accurately identified, extracted and presented. 
Your role often intersects with technology and accounting, making you adept at using various financial software and understanding the nuances of financial statements.
The final output should be a structured JSON representation.
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)



In [80]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    retriever=vectordb.as_retriever(search_type="mmr"),
    return_source_documents=True,
    chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})
print('\n\nQuery:\n\n', query)
# print(result)
print('\n\nAnswer:\n\n', result["result"])



Query:

 Based on the consolidated income statement, spanning multiple years, extract all financial figures for each year and structure it into a machine-readable JSON format.


Answer:

 

{
  "FinancialData": {
    "2021": {
      "Revenue": 6122.3,
      "Cost of Sales": 4500.2,
      "Gross Profit": 1622.1,
      "Operating Expenses": 1000.5,
      "Operating Profit": 621.6,
      "Other Income": 200.2,
      "Profit Before Tax": 821.8,
      "Income Tax Expense": 200.5,
      "Net Profit": 621.3,
      "Other Comprehensive Income": 0.0,
      "Total Comprehensive Income": 621.3
    },
    "2020": {
      "Revenue": 5500.2,
      "Cost of Sales": 4000.1,
      "Gross Profit": 1500.1,
      "Operating Expenses": 900.3,
      "Operating Profit": 599.8,
      "Other Income": 150.2,
      "Profit Before Tax": 750.0,
      "Income Tax Expense": 175.0,
      "Net Profit": 575.0


## Prompt variation

In [81]:
query = "Provide the consolidated income statement for 2021 and 2022."

In [82]:
question=query
# Build prompt
template = """You have a role of a Financial Data Analyst: With a keen eye for numbers and the intricacies of financial statements,
you specialize in extracting, analyzing, and structuring financial data. Your expertise ensures that critical financial metrics from provided context are accurately identified, extracted and presented. 
Your role often intersects with technology and accounting, making you adept at using various financial software and understanding the nuances of financial statements.
The final output should be a structured JSON representation. For 
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)



In [83]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    retriever=vectordb.as_retriever(search_type="mmr"),
    return_source_documents=True,
    chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})
print('\n\nQuery:\n\n', query)
# print(result)
print('\n\nAnswer:\n\n', result["result"])
# print('\n\nResult:\n\n', result["source_documents"][0])



Query:

 Provide the consolidated income statement for 2021 and 2022.


Answer:

 

Consolidated Income Statement for 2021

Revenue: 7,393 HRK million
Cost of Goods Sold: 1,251 HRK million
Energy Costs: 126 HRK million
Cost of Raw Materials and Supplies: 22 HRK million
Cost of Services Sold: 13 HRK million
Gross Profit: 5,981 HRK million
Operating Expenses: 2,845 HRK million
Operating Income: 3,136 HRK million
Interest Expense: 101 HRK million
Income Before Tax: 3,035 HRK million
Income Tax Expense: 891 HRK million
Net Income: 2,144 HRK million

Consolidated Income Statement for 2022

Revenue: 7,410 HRK million
Cost of Goods Sold: 1,278 HRK million
Energy Costs: 271 HRK million
Cost of Raw Materials and Supplies: 19 HRK million
Cost of Services Sold: 12 HRK million
Gross Profit: 5,930 HRK million
Operating Expenses: 2,845 HRK million
Operating Income: 3,085 HRK million
Interest Expense: 91 HRK million
Income Before Tax:


## Prompt variation

In [84]:
query = "Extract the key financial figures from consolidated income statement?"

In [85]:
question=query
# Build prompt
template = """Given a consolidated income statement's context or text spanning multiple years, 
please extract the essential financial information for each year. Ensure that all extractions are purely based on the data provided in the document. 
If a specific metric or data is not present in the provided context, the model should explicitly state that the information is "not available" or return "NaN" (Not a Number). 
Under no circumstances should the model generate or fabricate information not present in the document. 
Provide the results in a machine-readable JSON format.

{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)



In [86]:
 # Run chain
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
    llm,
    retriever=vectordb.as_retriever(search_type="mmr"),
    return_source_documents=True,
    chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
    )

result = qa_chain({"query": query})
print('\n\nQuery:\n\n', query)
# print(result)
print('\n\nAnswer:\n\n', result["result"])
print('\n\nResult:\n\n', result["source_documents"])



Query:

 Extract the key financial figures from consolidated income statement?


Answer:

 
{
  "2022": {
    "Revenue": 7410,
    "Segment Profit": 946,
    "Finance Income": 29,
    "Finance Cost": 91,
    "Profit Before Income Tax": 884,
    "Revenue from Rendering of Services": 6071,
    "Revenue from Sale of Goods and Merchandise": 1339,
    "Revenue Realized Over Time": 6080,
    "Revenue Realized at Point in Time": 1330,
    "Domestic Interconnection": 209,
    "International Interconnection": 311,
    "Copyright Fees": 91,
    "Online Services": 29,
    "Cleaning Services": 16,
    "Bank and Money Transfer Fees": 13,
    "Security Services": 12,
    "Other Services": 69,
    "Purchase Cost of Goods Sold": 1278,
    "Energy Costs": 271,
    "Cost of Raw Material and Supplies": 19,
    "Cost of Services Sold": 12,
    "Other Comprehensive Income for the Year from Continuing Operations, Net of Tax": 2,
    "Total Comprehensive Income


Result:

 [Document(page_content='Consolida

# Chat with PDF financial report

In [87]:
from langchain.vectorstores import Chroma
from langchain.embeddings.openai import OpenAIEmbeddings
# Define HT report persist directory
persist_directory = "../notebooks"
embedding = OpenAIEmbeddings()
vectordb = Chroma(persist_directory=persist_directory, embedding_function=embedding)

In [88]:
question = "Name financial stetements included into the HT financial report for 2021 and 2022?"
docs = vectordb.similarity_search(question,k=3)
len(docs)

3

In [89]:
docs

[Document(page_content='3CONTENT\nINTRODUCTION\nLETTER TO SHAREHOLDERS\nCORPORATE PROFILE\nINVESTOR INFORMATION\nMANAGEMENT BOARD\nSUPERVISORY BOARD\nCORPORATE GOVERNANCE CODE COMPLIANCE STATEMENT\nSUPERVISORY BOARD REPORT\nECONOMIC ENVIRONMENT, MARKET AND REGULATORY OVERVIEW\nECONOMIC BACKGROUND\nCROATIAN MARKET OVERVIEW\nREGULATORY OVERVIEW\nCHANGES IN REPORTING\nBUSINESS REVIEW\nSUMMARY OF KEY FINANCIAL INDICATORS\nHT GROUP HIGHLIGHTS\nMAIN FINANCIALS DEVELOPMENT\nCORPORATE SOCIAL RESPONSIBILITY\nHT GROUP FINANCIAL STATEMENTS\nCONSOLIDATED INCOME STATEMENT\nCONSOLIDATED BALANCE SHEET\nCONSOLIDATED CASH FLOW STATEMENT\nCONSOLIDATED FINANCIAL STATEMENTS\nINDEPENDENT AUDITOR’S REPORT \nRESPONSIBILITY FOR THE CONSOLIDATED FINANCIAL STATEMENTS\nCONSOLIDATED STATEMENT OF COMPREHENSIVE INCOME\nCONSOLIDATED STATEMENT OF FINANCIAL POSITION\nCONSOLIDATED STATEMENT OF CASH FLOWS\nCONSOLIDATED STATEMENT OF CHANGES IN EQUITY\nNOTES TO THE CONSOLIDATED FINANCIAL STATEMENTS\nThis format of the Ann

In [93]:
from langchain.chat_models import ChatOpenAI
llm_name = "gpt-3.5-turbo"
llm = ChatOpenAI(model_name=llm_name, temperature=0)
llm.predict("Hello world!")

'Hello! How can I assist you today?'

In [94]:
# Build prompt
from langchain.prompts import PromptTemplate
template = """Use the following pieces of context to answer the question at the end. 
If you don't know the answer, just say that you don't know, don't try to make up an answer. 
Use three sentences maximum. Keep the answer as concise as possible. 
Always say "thanks for asking!" at the end of the answer. 
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate(input_variables=["context", "question"],template=template,)

# Run chain
from langchain.chains import RetrievalQA
question = "List al financial statements from the HT financial report?"
qa_chain = RetrievalQA.from_chain_type(llm,
                                       retriever=vectordb.as_retriever(),
                                       return_source_documents=True,
                                       chain_type_kwargs={"prompt": QA_CHAIN_PROMPT})


result = qa_chain({"query": question})
result["result"]

'Consolidated income statement, consolidated balance sheet, consolidated cash flow statement, consolidated statement of comprehensive income, consolidated statement of financial position, consolidated statement of cash flows, consolidated statement of changes in equity. Thanks for asking!'

### Define memory

In [95]:
from langchain.memory import ConversationBufferMemory
memory = ConversationBufferMemory(
    memory_key="chat_history",
    return_messages=True
)

In [96]:
from langchain.chains import ConversationalRetrievalChain
retriever=vectordb.as_retriever()
qa = ConversationalRetrievalChain.from_llm(
    llm,
    retriever=retriever,
    memory=memory
)

In [100]:
question = "List finanacial position in the consolidated income statement for HT in 2021?"
result = qa({"question": question})

In [101]:
result['answer']

'The consolidated income statement does not provide specific information about the financial position of HT in 2021. It primarily focuses on the revenue, operating expenses, and net profit of the company. For detailed information about the financial position, you would need to refer to the consolidated balance sheet.'

In [99]:
question = "why are those prerequesites needed?"
result = qa({"question": question})

In [ ]:
result['answer']

# Chatbot over PDF financial report

In [102]:
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.text_splitter import CharacterTextSplitter, RecursiveCharacterTextSplitter
from langchain.vectorstores import DocArrayInMemorySearch
from langchain.document_loaders import TextLoader
from langchain.chains import RetrievalQA,  ConversationalRetrievalChain
from langchain.memory import ConversationBufferMemory
from langchain.chat_models import ChatOpenAI
from langchain.document_loaders import TextLoader
from langchain.document_loaders import PyPDFLoader

import panel as pn
pn.extension()

In [126]:
llm_name = "gpt-3.5-turbo"

In [104]:
def load_db(file, chain_type, k):
    # Load documents
    loader = PyPDFLoader(file)
    documents = loader.load()
    # Split documents
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=1500, chunk_overlap=150)
    docs = text_splitter.split_documents(documents)
    # Define embedding
    embeddings = OpenAIEmbeddings()
    # Create vector database from data
    db = DocArrayInMemorySearch.from_documents(docs, embeddings)
    # define retriever
    retriever = db.as_retriever(search_type="similarity", search_kwargs={"k": k})
    # Create a chatbot chain. Memory is managed externally.
    qa = ConversationalRetrievalChain.from_llm(
        llm=ChatOpenAI(model_name=llm_name, temperature=0), 
        chain_type=chain_type, 
        retriever=retriever, 
        return_source_documents=True,
        return_generated_question=True,
    )
    return qa 


In [105]:
import panel as pn
import param

class cbfs(param.Parameterized):
    chat_history = param.List([])
    answer = param.String("")
    db_query  = param.String("")
    db_response = param.List([])
    
    def __init__(self,  **params):
        super(cbfs, self).__init__( **params)
        self.panels = []
        self.loaded_file = "../../data/HT_report.pdf"
        self.qa = load_db(self.loaded_file,"stuff", 4)
    
    def call_load_db(self, count):
        if count == 0 or file_input.value is None:  # init or no file specified :
            return pn.pane.Markdown(f"Loaded File: {self.loaded_file}")
        else:
            file_input.save("temp.pdf")  # local copy
            self.loaded_file = file_input.filename
            button_load.button_style="outline"
            self.qa = load_db("temp.pdf", "stuff", 4)
            button_load.button_style="solid"
        self.clr_history()
        return pn.pane.Markdown(f"Loaded File: {self.loaded_file}")

    def convchain(self, query):
        if not query:
            return pn.WidgetBox(pn.Row('User:', pn.pane.Markdown("", width=600)), scroll=True)
        result = self.qa({"question": query, "chat_history": self.chat_history})
        self.chat_history.extend([(query, result["answer"])])
        self.db_query = result["generated_question"]
        self.db_response = result["source_documents"]
        self.answer = result['answer'] 
        self.panels.extend([
            pn.Row('User:', pn.pane.Markdown(query, width=600)),
            pn.Row('ChatBot:', pn.pane.Markdown(self.answer, width=600, style={'background-color': '#F6F6F6'}))
        ])
        inp.value = ''  #clears loading indicator when cleared
        return pn.WidgetBox(*self.panels,scroll=True)

    @param.depends('db_query ', )
    def get_lquest(self):
        if not self.db_query :
            return pn.Column(
                pn.Row(pn.pane.Markdown(f"Last question to DB:", styles={'background-color': '#F6F6F6'})),
                pn.Row(pn.pane.Str("no DB accesses so far"))
            )
        return pn.Column(
            pn.Row(pn.pane.Markdown(f"DB query:", styles={'background-color': '#F6F6F6'})),
            pn.pane.Str(self.db_query )
        )

    @param.depends('db_response', )
    def get_sources(self):
        if not self.db_response:
            return 
        rlist=[pn.Row(pn.pane.Markdown(f"Result of DB lookup:", styles={'background-color': '#F6F6F6'}))]
        for doc in self.db_response:
            rlist.append(pn.Row(pn.pane.Str(doc)))
        return pn.WidgetBox(*rlist, width=600, scroll=True)

    @param.depends('convchain', 'clr_history') 
    def get_chats(self):
        if not self.chat_history:
            return pn.WidgetBox(pn.Row(pn.pane.Str("No History Yet")), width=600, scroll=True)
        rlist=[pn.Row(pn.pane.Markdown(f"Current Chat History variable", styles={'background-color': '#F6F6F6'}))]
        for exchange in self.chat_history:
            rlist.append(pn.Row(pn.pane.Str(exchange)))
        return pn.WidgetBox(*rlist, width=600, scroll=True)

    def clr_history(self,count=0):
        self.chat_history = []
        return 


# Create a chatbot

In [106]:
cb = cbfs()

file_input = pn.widgets.FileInput(accept='.pdf')
button_load = pn.widgets.Button(name="Load DB", button_type='primary')
button_clearhistory = pn.widgets.Button(name="Clear History", button_type='warning')
button_clearhistory.on_click(cb.clr_history)
inp = pn.widgets.TextInput( placeholder='Enter text here…')

bound_button_load = pn.bind(cb.call_load_db, button_load.param.clicks)
conversation = pn.bind(cb.convchain, inp) 


In [107]:

jpg_pane = pn.pane.Image( './img/convchain.jpg')


In [108]:


tab1 = pn.Column(
    pn.Row(inp),
    pn.layout.Divider(),
    pn.panel(conversation,  loading_indicator=True, height=300),
    pn.layout.Divider(),
)
tab2= pn.Column(
    pn.panel(cb.get_lquest),
    pn.layout.Divider(),
    pn.panel(cb.get_sources ),
)
tab3= pn.Column(
    pn.panel(cb.get_chats),
    pn.layout.Divider(),
)
tab4=pn.Column(
    pn.Row( file_input, button_load, bound_button_load),
    pn.Row( button_clearhistory, pn.pane.Markdown("Clears chat history. Can use to start a new topic" )),
    pn.layout.Divider(),
    pn.Row(jpg_pane.clone(width=400))
)


In [109]:

dashboard = pn.Column(
    pn.Row(pn.pane.Markdown('# ChatWithYourData_Bot')),
    pn.Tabs(('Conversation', tab1), ('Database', tab2), ('Chat History', tab3),('Configure', tab4))
)

dashboard

BokehModel(combine_events=True, render_bundle={'docs_json': {'6a157bea-e2d2-4357-baa9-a47d90b6a145': {'version…

C:\Users\ggvozden\AppData\Local\Temp\ipykernel_15796\735518923.py:38: PanelDeprecationWarning: 'style' is deprecated and will be removed in version 1.3, use 'styles' instead.
  pn.Row('ChatBot:', pn.pane.Markdown(self.answer, width=600, style={'background-color': '#F6F6F6'}))
C:\Users\ggvozden\AppData\Local\Temp\ipykernel_15796\735518923.py:38: PanelDeprecationWarning: 'style' is deprecated and will be removed in version 1.3, use 'styles' instead.
  pn.Row('ChatBot:', pn.pane.Markdown(self.answer, width=600, style={'background-color': '#F6F6F6'}))
C:\Users\ggvozden\AppData\Local\Temp\ipykernel_15796\735518923.py:38: PanelDeprecationWarning: 'style' is deprecated and will be removed in version 1.3, use 'styles' instead.
  pn.Row('ChatBot:', pn.pane.Markdown(self.answer, width=600, style={'background-color': '#F6F6F6'}))
C:\Users\ggvozden\AppData\Local\Temp\ipykernel_15796\735518923.py:38: PanelDeprecationWarning: 'style' is deprecated and will be removed in version 1.3, use 'styles' ins